In [1]:
import os
import sys
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from scipy.integrate import odeint
import plotly.graph_objects as go
import plotly.io as pio
import requests
from lmfit import minimize, Parameters, Parameter, report_fit
from itertools import zip_longest
pio.renderers.default = "notebook"
%matplotlib inline
plt.style.use('ggplot')

In [2]:
from IPython.display import HTML
from ipywidgets.widgets import interact, IntSlider, FloatSlider, Layout, ToggleButton

style = {'description_width': '100px'}
slider_layout = Layout(width='99%')

In [3]:
def ode_model(z, t, beta, alpha, gamma, d, b, k, eps):
    """
    Reference https://www.idmod.org/docs/hiv/model-seir.html
    """
    S, E, I, Q, R = z
    N = S + E + I + Q + R
    dSdt = -beta*S*(I)/N
    dEdt = beta*S*(I)/N - (alpha+k)*E
    dIdt = alpha*E - (gamma+b)*I
    dQdt = b*I-(eps)*Q
#     dRdt = gamma*I
    dRdt = gamma*I+k*E+eps*Q
    return [dSdt, dEdt, dIdt, dQdt, dRdt]

In [4]:
def ode_solver(t, initial_conditions, params):
    initE, initI, initQ, initR, initN = initial_conditions
    beta, alpha, gamma, d, b, k, eps = params['beta'].value, params['alpha'].value, params['gamma'].value, params['d'].value, params['b'].value, params['k'].value, params['eps'].value
    initS = initN - (initE + initI + initR + initQ)
    res = odeint(ode_model, [initS, initE, initI, initQ, initR], t, args=(beta, alpha, gamma, d, b, k, eps))
    return res

In [5]:
response = requests.get('https://api.rootnet.in/covid19-in/stats/history')
print('Request Success? {}'.format(response.status_code == 200))
covid_history = response.json()['data']
print(covid_history)

Request Success? True
[{'day': '2020-03-10', 'summary': {'total': 47, 'confirmedCasesIndian': 31, 'confirmedCasesForeign': 16, 'discharged': 0, 'deaths': 0, 'confirmedButLocationUnidentified': 0}, 'regional': [{'loc': 'Delhi', 'confirmedCasesIndian': 4, 'confirmedCasesForeign': 0, 'discharged': 0, 'deaths': 0, 'totalConfirmed': 4}, {'loc': 'Haryana', 'confirmedCasesIndian': 0, 'confirmedCasesForeign': 14, 'discharged': 0, 'deaths': 0, 'totalConfirmed': 14}, {'loc': 'Karnataka', 'confirmedCasesIndian': 1, 'confirmedCasesForeign': 0, 'discharged': 0, 'deaths': 0, 'totalConfirmed': 1}, {'loc': 'Kerala', 'confirmedCasesIndian': 9, 'confirmedCasesForeign': 0, 'discharged': 0, 'deaths': 0, 'totalConfirmed': 9}, {'loc': 'Maharashtra', 'confirmedCasesIndian': 2, 'confirmedCasesForeign': 0, 'discharged': 0, 'deaths': 0, 'totalConfirmed': 2}, {'loc': 'Punjab', 'confirmedCasesIndian': 1, 'confirmedCasesForeign': 0, 'discharged': 0, 'deaths': 0, 'totalConfirmed': 1}, {'loc': 'Rajasthan', 'confirme

In [6]:
keys = ['day', 'total', 'confirmedCasesIndian', 'confirmedCasesForeign', 'confirmedButLocationUnidentified',
        'discharged', 'deaths']
df_covid_history = pd.DataFrame([[d.get('day'), 
                                  d['summary'].get('total'), 
                                  d['summary'].get('confirmedCasesIndian'), 
                                  d['summary'].get('confirmedCasesForeign'),
                                  d['summary'].get('confirmedButLocationUnidentified'),
                                  d['summary'].get('discharged'), 
                                  d['summary'].get('deaths')] 
                                 for d in covid_history],
                    columns=keys)
df_covid_history = df_covid_history.sort_values(by='day')
df_covid_history['infected'] = df_covid_history['total'] - df_covid_history['discharged'] - df_covid_history['deaths']
df_covid_history['total_recovered_or_dead'] = df_covid_history['discharged'] + df_covid_history['deaths']

In [7]:
# ref: https://www.medrxiv.org/content/10.1101/2020.04.01.20049825v1.full.pdf
initN = 1380000000
# S0 = 966000000
initE = 1000
initI = 47
initQ = 0
initR = 0
alpha = 1/5.2
gamma = 1/2.9
d = 0.00001
b = 1/3
k = 1/2.9
eps = 1/2.1
R0 = 4
beta = R0 * (d+alpha+k)*(d+gamma+b)/alpha
days = 112

params = Parameters()
params.add('beta', value=beta, min=0, max=10)
params.add('alpha', value=alpha, min=0, max=10)
params.add('gamma', value=gamma, min=0, max=10)
params.add('d', value=d, min=0, max=10)
params.add('b', value=b, min=0, max=10)
params.add('k', value=k, min=0, max=10)
params.add('eps', value=eps, min=0, max=10)

In [8]:
def main(initE, initI, initQ, initR, initN, beta, alpha, gamma, d, b, k, eps, days, param_fitting):
    initial_conditions = [initE, initI, initQ, initR, initN]
    params['beta'].value, params['alpha'].value,params['gamma'].value, params['d'].value, params['b'].value, params['k'].value, params['eps'].value = [beta, alpha, gamma, d, b, k, eps]
    tspan = np.arange(0, days, 1)
    sol = ode_solver(tspan, initial_conditions, params)
    S, E, I, Q, R = sol[:, 0], sol[:, 1], sol[:, 2], sol[:, 3], sol[:, 4]
    I_TOTAL = I + Q
    # Create traces
    fig = go.Figure()
    if not param_fitting:
        fig.add_trace(go.Scatter(x=tspan, y=S, mode='lines+markers', name='Вразливі'))
        fig.add_trace(go.Scatter(x=tspan, y=E, mode='lines+markers', name='В інкубаційному періоді'))
        fig.add_trace(go.Scatter(x=tspan, y=Q, mode='lines+markers', name='Госпіталізовані'))
        fig.add_trace(go.Scatter(x=tspan, y=I, mode='lines+markers', name='Інфіковані'))

    fig.add_trace(go.Scatter(x=tspan, y=R, mode='lines+markers',name='Одужавші/померлі'))
    if param_fitting:
        fig.add_trace(go.Scatter(x=tspan, y=I_TOTAL, mode='lines+markers', name='обрахована кількість Ііфікованих'))
        fig.add_trace(go.Scatter(x=tspan, y=df_covid_history.infected, mode='lines+markers',\
                             name='Інфіковані', line = dict(dash='dash')))
        fig.add_trace(go.Scatter(x=tspan, y=df_covid_history.total_recovered_or_dead, mode='lines+markers',\
                             name='Одужавші/померлі', line = dict(dash='dash')))
    
    if days <= 30:
        step = 1
    elif days <= 90:
        step = 7
    else:
        step = 30
    
    # Edit the layout
    fig.update_layout(title='Симуляція SEIQR моделі',
                       xaxis_title='Дні',
                       yaxis_title='Число осіб',
                       title_x=0.5,
                      width=900, height=600
                     )
    fig.update_xaxes(tickangle=-90, tickformat = None, tickmode='array', tickvals=np.arange(0, days + 1, step))
    if not os.path.exists("images"):
        os.mkdir("images")
    fig.write_image("images/seir_simulation(2).png")
    fig.show()

In [9]:
interact(main, initE=IntSlider(min=0, max=100000, step=1, value=initE, description='initE', style=style, \
                               layout=slider_layout),
               initI=IntSlider(min=0, max=100000, step=10, value=initI, description='initI', style=style, \
                               layout=slider_layout),
               initQ=IntSlider(min=0, max=100000, step=10, value=initQ, description='initQ', style=style, \
                               layout=slider_layout),
               initR=IntSlider(min=0, max=100000, step=10, value=initR, description='initR', style=style, \
                               layout=slider_layout),
               initN=IntSlider(min=0, max=138000, step=100, value=initN, description='initN', style=style, \
                               layout=slider_layout),
               beta=FloatSlider(min=0, max=4, step=0.01, value=beta, description='Infection rate', style=style, \
                                layout=slider_layout),
               alpha=FloatSlider(min=0, max=4, step=0.01, value=alpha, description='Incubation rate', style=style, \
                                 layout=slider_layout),
               gamma=FloatSlider(min=0, max=4, step=0.01, value=gamma, description='Recovery rate', style=style, \
                                 layout=slider_layout),
               d = FloatSlider(min=0, max=4, step=0.01, value=d, description='Natural death rate', style=style, \
                                 layout=slider_layout),
               b = FloatSlider(min=0, max=4, step=0.01, value=b, description='Hospitalisation rate', style=style, \
                                 layout=slider_layout),
               k = FloatSlider(min=0, max=4, step=0.01, value=k, description='Exposed recovery rate', style=style, \
                                 layout=slider_layout),
               eps = FloatSlider(min=0, max=4, step=0.01, value=eps, description='Hospitalised recovery rate', style=style, \
                                 layout=slider_layout),
               days=IntSlider(min=0, max=600, step=7, value=days, description='Days', style=style, \
                              layout=slider_layout),
               param_fitting=ToggleButton(value=False, description='Fitting Mode', disabled=False, button_style='', \
             tooltip='Click to show fewer plots', icon='check-circle')
        );

interactive(children=(IntSlider(value=1000, description='initE', layout=Layout(width='99%'), max=100000, style…

In [10]:
def error(params, initial_conditions, tspan, data):
    sol = ode_solver(tspan, initial_conditions, params)
    print("DATA!!!!!!!!!!")
    print(data)
    I = sol[:, 2]
    Q = sol[:, 3]
    R = sol[:, 4]
    res = np.array([[x+y,z] for x,y,z in zip_longest(I,Q,R)])
    print("EQUATION SOLUTION!!!!!!!!!!!!!!")
    print(sol)
    print("SLICE!!!!!!!!!")
    print(sol[:, 2:5:2])
    print("NOW THE DIFFERENCE!!!!!!!!!!!!")
    print((res - data).ravel())
    return (res - data).ravel()

In [11]:
initial_conditions = [initE, initI, initQ, initR, initN]
beta = 0.46
alpha = 0.19
gamma = 0.02
d = 0
b = 0.21
k = 0.01
eps = 0.03
params['beta'].value = beta
params['alpha'].value = alpha
params['gamma'].value = gamma
params['d'].value = d
params['b'].value = b
params['k'].value = k
params['eps'].value = eps
days = 50
tspan = np.arange(0, days, 1)
data = df_covid_history.loc[0:(days-1), ['infected', 'total_recovered_or_dead']].values

In [12]:
params

Parameters([('beta', <Parameter 'beta', value=0.46, bounds=[0:10]>),
            ('alpha', <Parameter 'alpha', value=0.19, bounds=[0:10]>),
            ('gamma', <Parameter 'gamma', value=0.02, bounds=[0:10]>),
            ('d', <Parameter 'd', value=0, bounds=[0:10]>),
            ('b', <Parameter 'b', value=0.21, bounds=[0:10]>),
            ('k', <Parameter 'k', value=0.01, bounds=[0:10]>),
            ('eps', <Parameter 'eps', value=0.03, bounds=[0:10]>)])

In [13]:
result = minimize(error, params, args=(initial_conditions, tspan, data), method='leastsq')

DATA!!!!!!!!!!
[[   47     0]
 [   60     0]
 [   73     0]
 [   70    12]
 [   72    12]
 [   95    15]
 [   99    15]
 [  120    17]
 [  134    17]
 [  149    24]
 [  196    27]
 [  256    27]
 [  329    31]
 [  424    43]
 [  469    50]
 [  553    53]
 [  634    60]
 [  640    84]
 [  810    99]
 [  901   123]
 [ 1118   133]
 [ 1238   159]
 [ 1649   185]
 [ 1860   209]
 [ 2322   225]
 [ 2784   288]
 [ 3219   358]
 [ 3851   430]
 [ 4312   477]
 [ 4714   560]
 [ 5218   647]
 [ 6039   722]
 [ 6634   895]
 [ 7409  1038]
 [ 8048  1304]
 [ 9272  1543]
 [10197  1736]
 [10824  1935]
 [11616  2219]
 [12289  2503]
 [13295  2821]
 [14255  3401]
 [15122  3863]
 [15859  4612]
 [16689  5011]
 [17915  5537]
 [18953  5989]
 [20177  6740]
 [21132  7248]
 [22010  7964]]
EQUATION SOLUTION!!!!!!!!!!!!!!
[[1.37999895e+09 1.00000000e+03 4.70000000e+01 0.00000000e+00
  0.00000000e+00]
 [1.37999890e+09 8.72105564e+02 1.94494159e+02 2.60555788e+01
  1.21101812e+01]
 [1.37999878e+09 8.18355267e+02 2.97007448

[[4.70000000e+01 0.00000000e+00]
 [1.94494159e+02 1.21101878e+01]
 [2.97007446e+02 2.69778907e+01]
 [3.73721574e+02 4.51129778e+01]
 [4.36243325e+02 6.69287299e+01]
 [4.91643816e+02 9.27903992e+01]
 [5.44282425e+02 1.23045151e+02]
 [5.96901713e+02 1.58040905e+02]
 [6.51285084e+02 1.98138596e+02]
 [7.08652222e+02 2.43720563e+02]
 [7.69897283e+02 2.95196710e+02]
 [8.35732859e+02 3.53009419e+02]
 [9.06777485e+02 4.17637827e+02]
 [9.83609406e+02 4.89601821e+02]
 [1.06680017e+03 5.69466001e+02]
 [1.15693627e+03 6.57843745e+02]
 [1.25463373e+03 7.55401478e+02]
 [1.36054857e+03 8.62863230e+02]
 [1.47538498e+03 9.81015521e+02]
 [1.59990226e+03 1.11071263e+03]
 [1.73492121e+03 1.25288232e+03]
 [1.88133031e+03 1.40853197e+03]
 [2.04009210e+03 1.57875530e+03]
 [2.21224977e+03 1.76473960e+03]
 [2.39893420e+03 1.96777362e+03]
 [2.60137150e+03 2.18925606e+03]
 [2.82089111e+03 2.43070481e+03]
 [3.05893455e+03 2.69376704e+03]
 [3.31706494e+03 2.98022998e+03]
 [3.59697726e+03 3.29203276e+03]
 [3.900509

DATA!!!!!!!!!!
[[   47     0]
 [   60     0]
 [   73     0]
 [   70    12]
 [   72    12]
 [   95    15]
 [   99    15]
 [  120    17]
 [  134    17]
 [  149    24]
 [  196    27]
 [  256    27]
 [  329    31]
 [  424    43]
 [  469    50]
 [  553    53]
 [  634    60]
 [  640    84]
 [  810    99]
 [  901   123]
 [ 1118   133]
 [ 1238   159]
 [ 1649   185]
 [ 1860   209]
 [ 2322   225]
 [ 2784   288]
 [ 3219   358]
 [ 3851   430]
 [ 4312   477]
 [ 4714   560]
 [ 5218   647]
 [ 6039   722]
 [ 6634   895]
 [ 7409  1038]
 [ 8048  1304]
 [ 9272  1543]
 [10197  1736]
 [10824  1935]
 [11616  2219]
 [12289  2503]
 [13295  2821]
 [14255  3401]
 [15122  3863]
 [15859  4612]
 [16689  5011]
 [17915  5537]
 [18953  5989]
 [20177  6740]
 [21132  7248]
 [22010  7964]]
EQUATION SOLUTION!!!!!!!!!!!!!!
[[1.37999895e+09 1.00000000e+03 4.70000000e+01 0.00000000e+00
  0.00000000e+00]
 [1.37999775e+09 5.32618041e+02 1.79259431e+02 4.16018159e-03
  1.53636008e+03]
 [1.37999575e+09 7.55567608e+02 2.62755800

DATA!!!!!!!!!!
[[   47     0]
 [   60     0]
 [   73     0]
 [   70    12]
 [   72    12]
 [   95    15]
 [   99    15]
 [  120    17]
 [  134    17]
 [  149    24]
 [  196    27]
 [  256    27]
 [  329    31]
 [  424    43]
 [  469    50]
 [  553    53]
 [  634    60]
 [  640    84]
 [  810    99]
 [  901   123]
 [ 1118   133]
 [ 1238   159]
 [ 1649   185]
 [ 1860   209]
 [ 2322   225]
 [ 2784   288]
 [ 3219   358]
 [ 3851   430]
 [ 4312   477]
 [ 4714   560]
 [ 5218   647]
 [ 6039   722]
 [ 6634   895]
 [ 7409  1038]
 [ 8048  1304]
 [ 9272  1543]
 [10197  1736]
 [10824  1935]
 [11616  2219]
 [12289  2503]
 [13295  2821]
 [14255  3401]
 [15122  3863]
 [15859  4612]
 [16689  5011]
 [17915  5537]
 [18953  5989]
 [20177  6740]
 [21132  7248]
 [22010  7964]]
EQUATION SOLUTION!!!!!!!!!!!!!!
[[1.37999895e+09 1.00000000e+03 4.70000000e+01 0.00000000e+00
  0.00000000e+00]
 [1.37999872e+09 8.34078721e+02 3.50321064e+01 1.57082049e+02
  2.58628824e+02]
 [1.37999852e+09 6.91043967e+02 2.89833577

  6.44853471e+03]]
SLICE!!!!!!!!!
[[  47.            0.        ]
 [  47.35413694   91.31233567]
 [  47.64658647  184.23240196]
 [  47.94020032  278.76080058]
 [  48.23561431  374.90162689]
 [  48.5328465   472.65905597]
 [  48.83190643  572.0373433 ]
 [  49.13280658  673.04077995]
 [  49.43555844  775.67373111]
 [  49.74017324  879.94061216]
 [  50.04666181  985.84589605]
 [  50.35503596 1093.39411578]
 [  50.6653073  1202.58985911]
 [  50.97748745 1313.43778102]
 [  51.29158808 1425.94259476]
 [  51.60762099 1540.10907008]
 [  51.92559801 1655.94203671]
 [  52.2455311  1773.44638115]
 [  52.56743222 1892.62705327]
 [  52.89131346 2013.48906066]
 [  53.21718693 2136.03747341]
 [  53.54506487 2260.27742131]
 [  53.87495955 2386.21409521]
 [  54.20688335 2513.85274695]
 [  54.5408487  2643.19868943]
 [  54.87686812 2774.25729843]
 [  55.2149542  2907.03400818]
 [  55.5551196  3041.53431474]
 [  55.89737708 3177.76378045]
 [  56.24173946 3315.7280275 ]
 [  56.58821962 3455.43273659]
 [  5

...

DATA!!!!!!!!!!
[[   47     0]
 [   60     0]
 [   73     0]
 [   70    12]
 [   72    12]
 [   95    15]
 [   99    15]
 [  120    17]
 [  134    17]
 [  149    24]
 [  196    27]
 [  256    27]
 [  329    31]
 [  424    43]
 [  469    50]
 [  553    53]
 [  634    60]
 [  640    84]
 [  810    99]
 [  901   123]
 [ 1118   133]
 [ 1238   159]
 [ 1649   185]
 [ 1860   209]
 [ 2322   225]
 [ 2784   288]
 [ 3219   358]
 [ 3851   430]
 [ 4312   477]
 [ 4714   560]
 [ 5218   647]
 [ 6039   722]
 [ 6634   895]
 [ 7409  1038]
 [ 8048  1304]
 [ 9272  1543]
 [10197  1736]
 [10824  1935]
 [11616  2219]
 [12289  2503]
 [13295  2821]
 [14255  3401]
 [15122  3863]
 [15859  4612]
 [16689  5011]
 [17915  5537]
 [18953  5989]
 [20177  6740]
 [21132  7248]
 [22010  7964]]
EQUATION SOLUTION!!!!!!!!!!!!!!
[[1.37999895e+09 1.00000000e+03 4.70000000e+01 0.00000000e+00
  0.00000000e+00]
 [1.37999876e+09 1.10447120e+03 2.67104546e+01 1.07791436e+02
  4.34709962e+00]
 [1.37999859e+09 1.17649917e+03 2.78755039

[[1.37999895e+09 1.00000000e+03 4.70000000e+01 0.00000000e+00
  0.00000000e+00]
 [1.37999876e+09 1.10447121e+03 2.67104813e+01 1.07791683e+02
  4.34690721e+00]
 [1.37999859e+09 1.17649923e+03 2.78755339e+01 1.99560462e+02
  1.00789188e+01]
 [1.37999841e+09 1.25223200e+03 2.96562257e+01 2.95133952e+02
  1.77614531e+01]
 [1.37999821e+09 1.33281620e+03 3.15643514e+01 3.95281895e+02
  2.75019384e+01]
 [1.37999801e+09 1.41858560e+03 3.35955733e+01 5.00339983e+02
  3.94035288e+01]
 [1.37999779e+09 1.50987439e+03 3.57575149e+01 6.10653476e+02
  5.35762949e+01]
 [1.37999756e+09 1.60703775e+03 3.80585812e+01 7.26589033e+02
  7.01379337e+01]
 [1.37999731e+09 1.71045373e+03 4.05077243e+01 8.48536361e+02
  8.92142525e+01]
 [1.37999705e+09 1.82052467e+03 4.31144736e+01 9.76909719e+02
  1.10939684e+02]
 [1.37999677e+09 1.93767884e+03 4.58889709e+01 1.11214951e+03
  1.35457829e+02]
 [1.37999647e+09 2.06237202e+03 4.88420108e+01 1.25472395e+03
  1.62922036e+02]
 [1.37999615e+09 2.19508938e+03 5.198508

  6.72125334e+03]]
SLICE!!!!!!!!!
[[4.70000000e+01 0.00000000e+00]
 [2.67105149e+01 4.34679707e+00]
 [2.78755756e+01 1.00785589e+01]
 [2.96562767e+01 1.77607048e+01]
 [3.15644128e+01 2.75006595e+01]
 [3.35956462e+01 3.94015730e+01]
 [3.57576005e+01 5.35735118e+01]
 [3.80586808e+01 7.01341677e+01]
 [4.05078395e+01 8.92093433e+01]
 [4.31146058e+01 1.10933465e+02]
 [4.58891220e+01 1.35450129e+02]
 [4.88421826e+01 1.62912675e+02]
 [5.19852771e+01 1.93484817e+02]
 [5.53306344e+01 2.27341284e+02]
 [5.88912702e+01 2.64668534e+02]
 [6.26810372e+01 3.05665494e+02]
 [6.67146810e+01 3.50544354e+02]
 [7.10078941e+01 3.99531412e+02]
 [7.55773798e+01 4.52867966e+02]
 [8.04409163e+01 5.10811290e+02]
 [8.56174260e+01 5.73635634e+02]
 [9.11270470e+01 6.41633313e+02]
 [9.69912162e+01 7.15115876e+02]
 [1.03232747e+02 7.94415300e+02]
 [1.09875922e+02 8.79885356e+02]
 [1.16946589e+02 9.71902948e+02]
 [1.24472251e+02 1.07086961e+03]
 [1.32482189e+02 1.17721309e+03]
 [1.41007565e+02 1.29138905e+03]
 [1.50081

  6.72116268e+03]]
SLICE!!!!!!!!!
[[4.70000000e+01 0.00000000e+00]
 [2.67105212e+01 4.34679549e+00]
 [2.78755837e+01 1.00785131e+01]
 [2.96562871e+01 1.77605775e+01]
 [3.15644258e+01 2.75004127e+01]
 [3.35956622e+01 3.94011677e+01]
 [3.57576197e+01 5.35729077e+01]
 [3.80587036e+01 7.01333236e+01]
 [4.05078663e+01 8.92082164e+01]
 [4.31146371e+01 1.10932011e+02]
 [4.58891580e+01 1.35448303e+02]
 [4.88422240e+01 1.62910429e+02]
 [5.19853245e+01 1.93482101e+02]
 [5.53306883e+01 2.27338048e+02]
 [5.88913312e+01 2.64664725e+02]
 [6.26811061e+01 3.05661056e+02]
 [6.67147584e+01 3.50539228e+02]
 [7.10079809e+01 3.99525540e+02]
 [7.55774769e+01 4.52861283e+02]
 [8.04410247e+01 5.10803730e+02]
 [8.56175467e+01 5.73627129e+02]
 [9.11271812e+01 6.41623789e+02]
 [9.69913650e+01 7.15105257e+02]
 [1.03232911e+02 7.94403507e+02]
 [1.09876105e+02 8.79872305e+02]
 [1.16946791e+02 9.71888550e+02]
 [1.24472473e+02 1.07085377e+03]
 [1.32482433e+02 1.17719571e+03]
 [1.41007834e+02 1.29137003e+03]
 [1.50081

DATA!!!!!!!!!!
[[   47     0]
 [   60     0]
 [   73     0]
 [   70    12]
 [   72    12]
 [   95    15]
 [   99    15]
 [  120    17]
 [  134    17]
 [  149    24]
 [  196    27]
 [  256    27]
 [  329    31]
 [  424    43]
 [  469    50]
 [  553    53]
 [  634    60]
 [  640    84]
 [  810    99]
 [  901   123]
 [ 1118   133]
 [ 1238   159]
 [ 1649   185]
 [ 1860   209]
 [ 2322   225]
 [ 2784   288]
 [ 3219   358]
 [ 3851   430]
 [ 4312   477]
 [ 4714   560]
 [ 5218   647]
 [ 6039   722]
 [ 6634   895]
 [ 7409  1038]
 [ 8048  1304]
 [ 9272  1543]
 [10197  1736]
 [10824  1935]
 [11616  2219]
 [12289  2503]
 [13295  2821]
 [14255  3401]
 [15122  3863]
 [15859  4612]
 [16689  5011]
 [17915  5537]
 [18953  5989]
 [20177  6740]
 [21132  7248]
 [22010  7964]]
EQUATION SOLUTION!!!!!!!!!!!!!!
[[1.37999895e+09 1.00000000e+03 4.70000000e+01 0.00000000e+00
  0.00000000e+00]
 [1.37999876e+09 1.10447154e+03 2.67105214e+01 1.07791809e+02
  4.34679486e+00]
 [1.37999859e+09 1.17649993e+03 2.78755839

In [14]:
result.params

Parameters([('beta',
             <Parameter 'beta', value=6.286905867947797, bounds=[0:10]>),
            ('alpha',
             <Parameter 'alpha', value=0.08652256877670794, bounds=[0:10]>),
            ('gamma',
             <Parameter 'gamma', value=0.10322936863796262, bounds=[0:10]>),
            ('d', <Parameter 'd', value=0.0, bounds=[0:10]>),
            ('b', <Parameter 'b', value=3.4878475219926086, bounds=[0:10]>),
            ('k',
             <Parameter 'k', value=2.4712106971858105e-07, bounds=[0:10]>),
            ('eps',
             <Parameter 'eps', value=0.019084658914078068, bounds=[0:10]>)])

In [15]:
# display fitted statistics
report_fit(result)

[[Fit Statistics]]
    # fitting method   = leastsq
    # function evals   = 490
    # data points      = 100
    # variables        = 7
    chi-square         = 77065759.6
    reduced chi-square = 828664.082
    Akaike info crit   = 1369.49995
    Bayesian info crit = 1387.73614
##  Warning: uncertainties could not be estimated:
    d:      at boundary
[[Variables]]
    beta:   6.28690587 (init = 0.46)
    alpha:  0.08652257 (init = 0.19)
    gamma:  0.10322937 (init = 0.02)
    d:      0.00000000 (init = 0)
    b:      3.48784752 (init = 0.21)
    k:      2.4712e-07 (init = 0.01)
    eps:    0.01908466 (init = 0.03)


In [16]:
final = data + result.residual.reshape(data.shape)
fig = go.Figure()
fig.add_trace(go.Scatter(x=tspan, y=data[:, 0], mode='markers', name='Інфіковані ', line = dict(dash='dot')))
fig.add_trace(go.Scatter(x=tspan, y=data[:, 1], mode='markers', name='одужавші/померлі', line = dict(dash='dot')))
fig.add_trace(go.Scatter(x=tspan, y=final[:, 0], mode='lines+markers', name='обрахована кількість інфікованих'))
fig.add_trace(go.Scatter(x=tspan, y=final[:, 1], mode='lines+markers', name='обрахована кількість одужавших/померлих'))
fig.update_layout(title='Порівняння зпрогнозованих та реальних данних',
                       xaxis_title='Дні',
                       yaxis_title='Число осіб',
                       title_x=0.5,
                      width=1000, height=600
                     )



In [17]:
observed_IR = df_covid_history.loc[:, ['infected', 'total_recovered_or_dead']].values
print(observed_IR.shape)

(86, 2)


In [18]:
tspan_fit_pred = np.arange(0, observed_IR.shape[0], 1)
params['beta'].value = result.params['beta'].value
params['alpha'].value = result.params['alpha'].value
params['gamma'].value = result.params['gamma'].value
params['d'].value = result.params['d'].value
params['b'].value = result.params['b'].value
params['k'].value = result.params['k'].value
params['eps'].value = result.params['eps'].value
fitted_predicted = ode_solver(tspan_fit_pred, initial_conditions, params)

In [19]:
fitted_predicted_IR = fitted_predicted[:, 2:4]
print(fitted_predicted_IR.shape)

(86, 2)


In [20]:
print("Fitted MAE")
print('Infected: ', np.mean(np.abs(fitted_predicted_IR[:days, 0] - observed_IR[:days, 0])))
print('Recovered/Deceased: ', np.mean(np.abs(fitted_predicted_IR[:days, 1] - observed_IR[:days, 1])))

print("\nFitted RMSE")
print('Infected: ', np.sqrt(np.mean((fitted_predicted_IR[:days, 0] - observed_IR[:days, 0])**2)))
print('Recovered/Deceased: ', np.sqrt(np.mean((fitted_predicted_IR[:days, 1] - observed_IR[:days, 1])**2)))

Fitted MAE
Infected:  5757.390701272287
Recovered/Deceased:  4971.773072261093

Fitted RMSE
Infected:  8808.521187852795
Recovered/Deceased:  6415.18397343529


In [21]:
print("Predicted MAE")
print('Infected: ', np.mean(np.abs(fitted_predicted_IR[days:observed_IR.shape[0], 0] - observed_IR[days:, 0])))
print('Recovered/Deceased: ', np.mean(np.abs(fitted_predicted_IR[days:observed_IR.shape[0], 1] - observed_IR[days:, 1])))

print("\nPredicted RMSE")
print('Infected: ', np.sqrt(np.mean((fitted_predicted_IR[days:observed_IR.shape[0], 0] - observed_IR[days:, 0])**2)))
print('Recovered/Deceased: ', np.sqrt(np.mean((fitted_predicted_IR[days:observed_IR.shape[0], 1] - observed_IR[days:, 1])**2)))

Predicted MAE
Infected:  55116.68480930711
Recovered/Deceased:  43517.47417653619

Predicted RMSE
Infected:  59436.753482348366
Recovered/Deceased:  50300.69487808984


In [22]:
interact(main, initE=IntSlider(min=0, max=100000, step=1, value=initE, description='initE', style=style, \
                               layout=slider_layout),
               initI=IntSlider(min=0, max=100000, step=10, value=initI, description='initI', style=style, \
                               layout=slider_layout),
               initQ=IntSlider(min=0, max=100000, step=10, value=initQ, description='initQ', style=style, \
                               layout=slider_layout),
               initR=IntSlider(min=0, max=100000, step=10, value=initR, description='initR', style=style, \
                               layout=slider_layout),
               initN=IntSlider(min=0, max=1380000000, step=1000, value=initN, description='initN', style=style, \
                               layout=slider_layout),
               beta=FloatSlider(min=0, max=7, step=0.01, value=result.params['beta'].value, description='Infection rate', style=style, \
                                layout=slider_layout),
               alpha=FloatSlider(min=0, max=4, step=0.01, value=result.params['alpha'].value, description='Incubation rate', style=style, \
                                 layout=slider_layout),
               gamma=FloatSlider(min=0, max=4, step=0.01, value=result.params['gamma'].value, description='Recovery rate', style=style, \
                                 layout=slider_layout),
               d=FloatSlider(min=0, max=4, step=0.01, value=result.params['d'].value, description='Natural death rate', style=style, \
                                 layout=slider_layout),
               b=FloatSlider(min=0, max=4, step=0.01, value=result.params['b'].value, description='Hospitalisation rate', style=style, \
                                 layout=slider_layout),
               k=FloatSlider(min=0, max=4, step=0.01, value=result.params['k'].value, description='Exposed recovery rate', style=style, \
                                 layout=slider_layout),
               eps=FloatSlider(min=0, max=4, step=0.01, value=result.params['eps'].value, description='Hospitalised recovery rate', style=style, \
                                 layout=slider_layout),
               days=IntSlider(min=0, max=600, step=7, value=240, description='Days', style=style, \
                              layout=slider_layout),
               param_fitting=ToggleButton(value=False, description='Fitting Mode', disabled=True, button_style='', \
             tooltip='Click to show fewer plots', icon='check-circle')
        );

interactive(children=(IntSlider(value=1000, description='initE', layout=Layout(width='99%'), max=100000, style…